# Clean Human Pose MPI Dataset

Fix data

Data structure:
- `data[2]` = 2 x 7 x 100 array
- `data[2][0]` = x locations
- `data[2][0]` = y locations
- ordering is `0 Head, 1 Right wrist, 2 Left wrist, 3 Right elbow, 4 Left elbow, 5 Right shoulder and 6 Left shoulder`

In [175]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
import math
from glob import glob
from random import randint

import cv2 as cv
import numpy as np
import pandas as pd
from PIL import Image, ImageDraw
%matplotlib inline
import matplotlib.pyplot as plt
import scipy.io
from pathlib import Path
from sklearn import preprocessing

import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.settings import app_cfg as cfg
from app.utils import file_utils

In [176]:
DATA_STORE = '/data_store_nas/'
fp_dataset = join(DATA_STORE, 'datasets/people/youtube_poses')
dir_fp_frames = join(fp_dataset, 'YouTube_Pose_dataset_1.0/GT_frames')

In [177]:
dirs_frames = glob(join(dir_fp_frames, '*'))
fps_frames = {}
for dir_frames in dirs_frames:
  fps_frames[dir_frames] = join(dir_frames, '*')

In [178]:
fp_pose_data = join(fp_dataset, 'YouTube_Pose_dataset_1.0/YouTube_Pose_dataset.mat')
fp_out = join(fp_dataset, 'poses.csv')
pose_data = scipy.io.loadmat(fp_pose_data)['data'][0]

In [182]:
# convert data to pandas DF for sanity
poses = []
for i, pose in enumerate(pose_data):

  video_id = pose[1][0]
  pose_pts = pose[2]
  crop_x1 = int(pose[6][0][0])
  crop_y1 = int(pose[6][0][1])
  crop_x2 = int(pose[6][0][2])
  crop_y2 = int(pose[6][0][3])
  w = pose[7][0][0]
  h = pose[7][0][1]
  scale = pose[5][0][0]
  
  for j in range(pose_pts.shape[2]): # 100 frames
    x = [pose_pts[0][i][j] for i in range(7)]
    y = [pose_pts[1][i][j] for i in range(7)]
    poses.append({
      'video_id': video_id, 
      'scale': scale,
      'crop_x1': crop_x1,
      'crop_y1': crop_y1,
      'crop_x2': crop_x2,
      'crop_y2': crop_y2,
      'width': w, 
      'height': h,
      'head_x': x[0],
      'head_y': y[0],
      'wrist_right_x': x[1],
      'wrist_right_y': y[1],
      'wrist_left_x': x[2], 
      'wrist_left_y': y[2],
      'elbow_right_x': x[3],
      'elbow_right_y': y[3],
      'elbow_left_x': x[4], 
      'elbow_left_y': y[4],
      'shoulder_right_x': x[5],
      'shoulder_right_y': y[5],
      'shoulder_left_x': x[6], 
      'shoulder_left_y':  y[6],
      })
df_poses = pd.DataFrame.from_dict(poses)
df_poses.to_csv(fp_out)

In [183]:
df_poses.head()

crop_x1  crop_x2  crop_y1  crop_y2  elbow_left_x  elbow_left_y  \
0        1     1920        1     1080    277.721438    192.416331   
1        1     1920        1     1080    273.497648    187.629368   
2        1     1920        1     1080    258.010417    159.752352   
3        1     1920        1     1080    274.342406    188.192540   
4        1     1920        1     1080    272.371304    194.387433   

   elbow_right_x  elbow_right_y      head_x     head_y      ...        \
0     147.628696     169.326277  195.498320  81.471438      ...         
1     152.134073     129.341062  207.324933  72.742272      ...         
2     160.581653     143.138777  229.007056  76.966062      ...         
3     142.841734     110.193212  203.101142  76.402890      ...         
4     225.628024     164.820901  245.902218  93.016465      ...         

   shoulder_left_x  shoulder_left_y  shoulder_right_x  shoulder_right_y  \
0       254.631384       127.088374        178.603159        134.691196   
1       254.349798       131.593750        181.137433        123.990927   
2       250.407594       125.117272        190.992944        117.232863   
3       253.786626       128.777890        185.361223        120.611895   
4       255.476142       139.478159        183.390121        126.806788   

      video_id  width wrist_left_x  wrist_left_y  wrist_right_x  wrist_right_y  
0  -osma2n86oA    720   278.566196    235.498992     158.047379     122.301411  
1  -osma2n86oA    720   274.342406    235.498992     135.238911      91.608535  
2  -osma2n86oA    720   213.801411    108.785282     181.982191      89.074261  
3  -osma2n86oA    720   276.595094    231.556788     156.921035      55.847110  
4  -osma2n86oA    720   305.316868    172.423723     278.284610     165.102487  

[5 rows x 22 columns]

In [172]:
len(df_poses.keys())

22